Dado:

    Habitación de MxN espacios.
    Número de agentes.
    Porcentaje de celdas inicialmente sucias.
    Tiempo máximo de ejecución.

Realiza la siguiente simulación:

    Inicializa las celdas sucias (ubicaciones aleatorias).
    Todos los agentes empiezan en la celda [1,1].
    En cada paso de tiempo:
        Si la celda está sucia, entonces aspira.
        Si la celda está limpia, el agente elije una dirección aleatoria para moverse (unas de las 8 celdas vecinas) y elije la acción de movimiento (si no puede moverse allí, permanecerá en la misma celda).
    Se ejecuta el tiempo máximo establecido.


In [ ]:
!pip install mesa
from mesa import Agent, Model

from mesa.space import MultiGrid

from mesa.time import SimultaneousActivation

from mesa.datacollection import DataCollector

%matplotlib

import matplotlib
import matplotlib.pyplot as plt
import matplotlib.animation as animation
plt.rcParams["animation.html"] = "jshtml"
matplotlib.rcParams['animation.embed_limit'] = 2**128

import numpy as np
import pandas as pd  

import time
import datetime

import random

Using matplotlib backend: agg


In [ ]:
def get_grid(model):
  grid = np.zeros((model.grid.width, model.grid.height))

  for cell in model.grid.coord_iter():
    
    cell_content, x , y = cell
    for obj in cell_content:
      if isinstance(obj, RobotLimpieza):
        grid[x][y] = 10
      elif isinstance(obj, Celda):
        grid[x][y] = obj.estado
  
  return grid;


class Celda(Agent):
  # 1 sucio 
  #0 limpio
  def __init__(self, unique_id, model, estado):
    super().__init__(unique_id, model)
    self.estado = estado
    self.pos = unique_id
    self.sig_estado = None

class RobotLimpieza (Agent):
    
    def __init__(self, unique_id, model):
        super().__init__(unique_id, model)
        self.sig_pos = None
        
    
    def step(self):
      
      vecinos = neighbours = self.model.grid.get_neighbors(
          self.pos,
          moore = True,
          include_center = True)
        #maquina de estados
      for vecino in vecinos:
        if isinstance(vecino, Celda) and self.pos == vecino.pos:
          if vecino.estado == 1:
            #limpiar
            vecino.sig_estado = 0
            self.sig_pos = self.pos
          else:
            vecinos_2 = vecinos = neighbours = self.model.grid.get_neighborhood(
                self.pos,
                moore = True,
                include_center = False)
            self.sig_pos = self.random.choice(vecinos_2)
            break
              

        #
    def advance(self):
      vecinos = neighbours = self.model.grid.get_neighbors(
        self.pos,
        moore = True,
        include_center = True)
      #maquina de estados
      for vecino in vecinos:
        if isinstance(vecino, Celda) and self.pos == vecino.pos:
          vecino.estado = vecino.sig_estado 
      self.model.grid.move_agent(self, self.sig_pos)


class Habitacion(Model):
    def __init__(self, M, N, num_agentes, porc_celdas_sucias):
        self.num_agentes = num_agentes
        self.porc_celdas_sucias = porc_celdas_sucias
        self.grid = MultiGrid(M, N, False)
        self.porc_celdas_limpias = 1 - porc_celdas_sucias
        self.schedule = SimultaneousActivation(self)

        num_celdas = (int(M*N*porc_celdas_sucias))
        #creacion de grid con celdas sucias y limpias
        for(content, x ,y) in self.grid.coord_iter():
          num = random.randint(0,1)
          if num == 1 and num_celdas > 0:
            a = Celda((x,y), self, 1)
            num_celdas -= 1
          else:
            a = Celda((x,y), self, 0)
          self.grid.place_agent(a, (x,y))
          self.schedule.add(a)
          
          
          #colocacion de robots
        for id in range(num_agentes):
          r = RobotLimpieza(id, self)
          self.grid.place_agent(r, (1,1))
          self.schedule.add(r)
        
        self.datacollector = DataCollector(
            model_reporters = {"Grid": get_grid})

    def step(self):
        self.datacollector.collect(self)
        self.schedule.step()

    def todoLimpio(self):
      for(content, x, y) in self.grid.coord_iter():
        for obj in content:
          if isinstance(obj, Celda) and obj.estado == 1:
            return False
      return True
    def celdasSucias(self):
      sucias = 0
      for(content, x, y) in self.grid.coord_iter():
        for obj in content:
          if isinstance(obj, Celda) and obj.estado == 1:
            sucias += 1
      return sucias

In [ ]:
M = 15
N = 10
num_agentes = 30
porc_celdas_sucias = 0.6
tiempo_maximo = 5



start_time = time.time()

for i in range(1,num_agentes+1):
  pasos = 0
  model = Habitacion(M, N, i, porc_celdas_sucias)
  while((time.time()-start_time) < tiempo_maximo and not model.todoLimpio()):
    pasos += 1
    model.step();
  print('Tiempo de ejecucion ',str(i), ' agentes :', str(datetime.timedelta(seconds=(time.time()-start_time))))
  print('Pasos con ',str(i), ' agentes :', str(pasos))
  print('Tiles sucias con ',str(i), ' agentes :', str(model.celdasSucias()))
  #print(str(pasos)) 


Tiempo de ejecucion  1  agentes : 0:00:00.400116
Pasos con  1  agentes : 1447
Tiles sucias con  1  agentes : 0
Tiempo de ejecucion  2  agentes : 0:00:00.622401
Pasos con  2  agentes : 692
Tiles sucias con  2  agentes : 0
Tiempo de ejecucion  3  agentes : 0:00:00.864236
Pasos con  3  agentes : 633
Tiles sucias con  3  agentes : 0
Tiempo de ejecucion  4  agentes : 0:00:01.056707
Pasos con  4  agentes : 536
Tiles sucias con  4  agentes : 0
Tiempo de ejecucion  5  agentes : 0:00:01.160398
Pasos con  5  agentes : 251
Tiles sucias con  5  agentes : 0
Tiempo de ejecucion  6  agentes : 0:00:01.295715
Pasos con  6  agentes : 280
Tiles sucias con  6  agentes : 0
Tiempo de ejecucion  7  agentes : 0:00:01.399831
Pasos con  7  agentes : 221
Tiles sucias con  7  agentes : 0
Tiempo de ejecucion  8  agentes : 0:00:01.508610
Pasos con  8  agentes : 205
Tiles sucias con  8  agentes : 0
Tiempo de ejecucion  9  agentes : 0:00:01.695999
Pasos con  9  agentes : 333
Tiles sucias con  9  agentes : 0
Tiempo de

In [ ]:
all_grid = model.datacollector.get_model_vars_dataframe()
print(all_grid)

                                                   Grid
0     [[1.0, 1.0, 0.0, 1.0, 0.0, 0.0, 0.0, 1.0, 0.0,...
1     [[1.0, 10.0, 0.0, 1.0, 0.0, 0.0, 0.0, 1.0, 0.0...
2     [[1.0, 10.0, 0.0, 1.0, 0.0, 0.0, 0.0, 1.0, 0.0...
3     [[10.0, 0.0, 0.0, 1.0, 0.0, 0.0, 0.0, 1.0, 0.0...
4     [[10.0, 0.0, 0.0, 1.0, 0.0, 0.0, 0.0, 1.0, 0.0...
...                                                 ...
2319  [[0.0, 0.0, nan, 0.0, nan, nan, nan, 0.0, nan,...
2320  [[0.0, 0.0, nan, 0.0, nan, nan, nan, 0.0, nan,...
2321  [[0.0, 0.0, nan, 0.0, nan, nan, nan, 0.0, nan,...
2322  [[0.0, 0.0, nan, 0.0, nan, nan, nan, 0.0, nan,...
2323  [[0.0, 0.0, nan, 0.0, nan, nan, nan, 0.0, nan,...

[2324 rows x 1 columns]


In [ ]:
%%capture

fig, axs = plt.subplots(figsize=(7,7))
axs.set_xticks([])
axs.set_yticks([])
patch = plt.imshow(all_grid.iloc[0][0],cmap=plt.cm.binary)


def animate(i):
  patch.set_data(all_grid.iloc[i][0])

anim = animation.FuncAnimation(fig, animate, frames=len(all_grid))

In [ ]:
anim